In [2]:
import torch
import torch.nn.functional as F
import matplotlib.pyplot as plt
%matplotlib inline


In [3]:
# read in all the words
words = open('names.txt', 'r').read().splitlines()
words[:8]

['emma', 'olivia', 'ava', 'isabella', 'sophia', 'charlotte', 'mia', 'amelia']

In [4]:
len(words)

32033

In [5]:
# build the vocabulary of characters and mappings to/from integers
chars = sorted(list(set(''.join(words))))
stoi = {s:i+1 for i,s in enumerate(chars)}
stoi['.'] = 0
itos = {i:s for s,i in stoi.items()}
print(itos)

{1: 'a', 2: 'b', 3: 'c', 4: 'd', 5: 'e', 6: 'f', 7: 'g', 8: 'h', 9: 'i', 10: 'j', 11: 'k', 12: 'l', 13: 'm', 14: 'n', 15: 'o', 16: 'p', 17: 'q', 18: 'r', 19: 's', 20: 't', 21: 'u', 22: 'v', 23: 'w', 24: 'x', 25: 'y', 26: 'z', 0: '.'}


So we are making the dataset now

Always taking a word and padding it with dots. And then predicting the next token.

In [10]:
# build the dataset

block_size = 10 # context length: how many characters do we take to predict the next one?
X, Y = [], []
for w in words:

  #print(w)
  context = [0] * block_size
  for ch in w + '.':
    ix = stoi[ch]
    X.append(context)
    Y.append(ix)
    print(''.join(itos[i] for i in context), '--->', itos[ix])
    context = context[1:] + [ix] # crop and append

X = torch.tensor(X)
Y = torch.tensor(Y)

.......... ---> e
.........e ---> m
........em ---> m
.......emm ---> a
......emma ---> .
.......... ---> o
.........o ---> l
........ol ---> i
.......oli ---> v
......oliv ---> i
.....olivi ---> a
....olivia ---> .
.......... ---> a
.........a ---> v
........av ---> a
.......ava ---> .
.......... ---> i
.........i ---> s
........is ---> a
.......isa ---> b
......isab ---> e
.....isabe ---> l
....isabel ---> l
...isabell ---> a
..isabella ---> .
.......... ---> s
.........s ---> o
........so ---> p
.......sop ---> h
......soph ---> i
.....sophi ---> a
....sophia ---> .
.......... ---> c
.........c ---> h
........ch ---> a
.......cha ---> r
......char ---> l
.....charl ---> o
....charlo ---> t
...charlot ---> t
..charlott ---> e
.charlotte ---> .
.......... ---> m
.........m ---> i
........mi ---> a
.......mia ---> .
.......... ---> a
.........a ---> m
........am ---> e
.......ame ---> l
......amel ---> i
.....ameli ---> a
....amelia ---> .
.......... ---> h
.........h ---> a
........ha

In [13]:
X.shape, X.dtype, Y.shape, Y.dtype

(torch.Size([228146, 10]), torch.int64, torch.Size([228146]), torch.int64)

In [14]:
Y

tensor([ 5, 13, 13,  ..., 26, 24,  0])

In the paper they cram 17.000 words or so into only 30 dimensional space.

We only have 27 charachters, so let's cram them into a 2 d space.

In [17]:
C = torch.randn((27, 2))

In [19]:
C

tensor([[ 1.4820,  0.8167],
        [ 1.0111, -0.8497],
        [-0.3569,  0.0387],
        [ 0.6771,  0.1573],
        [ 0.5894,  0.2321],
        [ 0.5547,  1.0453],
        [ 0.6945,  0.4041],
        [-0.7587,  0.7657],
        [-0.2991,  0.3045],
        [ 1.0523,  0.4966],
        [-1.3357,  0.4953],
        [ 0.5710, -0.4736],
        [ 1.7258,  0.8863],
        [ 1.4239, -0.4875],
        [ 1.1553,  0.9400],
        [ 0.1202,  0.2844],
        [-0.1358,  1.2809],
        [ 0.3703, -0.3891],
        [ 0.8068,  0.0691],
        [-0.7599, -0.2901],
        [-0.8179, -0.1500],
        [-1.0814, -0.1978],
        [-0.6550,  1.2089],
        [ 0.1799, -0.5278],
        [ 2.0128,  1.8670],
        [-0.4815,  1.4739],
        [-1.9807, -0.2723]])

We could just set 5 to be `C[5]`

In [21]:
C[5]

tensor([0.5547, 1.0453])

In [25]:
F.one_hot(torch.tensor(5), num_classes=27)

tensor([0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0])